In [2]:
import os
import pandas as pd
from google.cloud import bigquery
import db_dtypes

#scenic-outcome-453219-h5-4c318c9a7175
os.environ["GOOGLE_APPLICATION_CREDENTIALS"]="scenic-outcome-453219-h5-4c318c9a7175.json"
client = bigquery.Client() 

pd.set_option('display.max_columns', None)  # wyłącz limit na kolumny
pd.set_option('display.max_rows', None)  # wyłącz limit na wiersze
pd.set_option('display.width', None)  # wyłącz limit na szerokość
pd.set_option('display.max_colwidth', None)  # wyłącz limit na szerokość kolumn
# client = bigquery.Client()

In [3]:
query = ('select * from bigquery-public-data.covid19_open_data.covid19_open_data limit 5')
query_job = client.query(query)
query_result = query_job.result()
df = query_result.to_dataframe()

KeyboardInterrupt: 

In [35]:
df

location_key        date                     place_id wikidata_id  \
0           AR  2021-06-28  ChIJZ8b99fXKvJURqA_wKpl3Lz0        Q414   
1           AR  2022-05-15  ChIJZ8b99fXKvJURqA_wKpl3Lz0        Q414   
2           AR  2020-05-21  ChIJZ8b99fXKvJURqA_wKpl3Lz0        Q414   
3           AR  2021-04-23  ChIJZ8b99fXKvJURqA_wKpl3Lz0        Q414   
4           AR  2021-04-02  ChIJZ8b99fXKvJURqA_wKpl3Lz0        Q414   

  datacommons_id country_code country_name iso_3166_1_alpha_2  \
0    country/ARG           AR    Argentina                 AR   
1    country/ARG           AR    Argentina                 AR   
2    country/ARG           AR    Argentina                 AR   
3    country/ARG           AR    Argentina                 AR   
4    country/ARG           AR    Argentina                 AR   

  iso_3166_1_alpha_3  aggregation_level  new_confirmed  new_deceased  \
0                ARG                  0          22444           397   
1                ARG                  0           2569             5   
2                ARG                  0            752            17   
3                ARG                  0          25991           460   
4                ARG                  0          11233           176   

   cumulative_confirmed  cumulative_deceased  cumulative_tested  \
0               4505477                99893           13199058   
1               9134570               128842           27925399   
2                 10850                  517             123508   
3               2903520                65960            9144055   
4               2419663                59705            7783414   

   new_persons_vaccinated  cumulative_persons_vaccinated  \
0                  136114                        7300645   
1                     216                       17629911   
2                    <NA>                           <NA>   
3                   81722                        2875049   
4                   30339                        1643728   

   new_persons_fully_vaccinated  cumulative_persons_fully_vaccinated  \
0                         21878                              1838327   
1                           712                             16023712   
2                          <NA>                                 <NA>   
3                          5575                               395309   
4                           473                               305848   

   new_vaccine_doses_administered  cumulative_vaccine_doses_administered  \
0                          157992                                9138972   
1                             928                               33653623   
2                            <NA>                                   <NA>   
3                           87297                                3270358   
4                           30812                                1949576   

   population  population_male  population_female  population_rural  \
0    44938712         19523766           20593330           3599141   
1    44938712         19523766           20593330           3599141   
2    44938712         19523766           20593330           3599141   
3    44938712         19523766           20593330           3599141   
4    44938712         19523766           20593330           3599141   

   population_urban  population_density  human_development_index  \
0          41339571              16.515                    0.825   
1          41339571              16.515                    0.825   
2          41339571              16.515                    0.825   
3          41339571              16.515                    0.825   
4          41339571              16.515                    0.825   

   population_age_00_09  population_age_10_19  population_age_20_29  \
0               6718871               7045513               6430658   
1               6718871               7045513               6430658   
2               6718871               7045513   

In [36]:
#Lista wszystkich kolumn
query = """
    SELECT column_name
    FROM `bigquery-public-data.covid19_open_data.INFORMATION_SCHEMA.COLUMNS`
    WHERE table_name = 'covid19_open_data'
    limit 5
"""
query_job = client.query(query)
columns_df = query_job.result().to_dataframe()

columns_df

column_name
0    location_key
1            date
2        place_id
3     wikidata_id
4  datacommons_id

In [37]:
# 3.1. Sprawdź, ile jest zapisanych wierszy z danymi.
query = "SELECT COUNT(*) AS row_count FROM `bigquery-public-data.covid19_open_data.covid19_open_data`"
query_job = client.query(query)
rows_df = query_job.result().to_dataframe()
rows_df

row_count
0   22756333

In [38]:
# 3.2. Sprawdź, ile krajów jest uwzględnionych w danych. 
query = "SELECT COUNT(DISTINCT country_name) AS country_count FROM `bigquery-public-data.covid19_open_data.covid19_open_data`"
query_job = client.query(query)
countries_df = query_job.result().to_dataframe()
countries_df

country_count
0            246

In [39]:
# # 3.3. Sprawdź, w jaki sposób zapisywane są dzienne informacje dla krajów.
#
# # Do pomocy, potem nadpisywane
# query = """
#     SELECT country_name, date, COUNT(*) AS records_per_day
#     FROM `bigquery-public-data.covid19_open_data.covid19_open_data`
#     WHERE country_name = 'Poland' AND new_confirmed IS NOT NULL
#     GROUP BY country_name, date
#     ORDER BY country_name, date
#     LIMIT 10
# """
#
# query = """
#     SELECT country_name, date, new_confirmed, new_deceased, cumulative_confirmed, cumulative_deceased, cumulative_tested
#     FROM `bigquery-public-data.covid19_open_data.covid19_open_data`
#     WHERE country_name = 'France' AND new_confirmed IS NOT NULL AND cumulative_confirmed != 0
#     ORDER BY country_name, date
#     LIMIT 10
# """
# # W Francji pierwsze zachorowania 22.01.2020
#
# query_job = client.query(query)
# daily_records_df = query_job.result().to_dataframe()
# daily_records_df

In [40]:
# # 3.4. Sprawdź, w jaki sposób zapisywane są wartości liczbowe.
# query = """
#     SELECT column_name, data_type
#     FROM bigquery-public-data.covid19_open_data.INFORMATION_SCHEMA.COLUMNS
#     WHERE table_name = 'covid19_open_data'
#     limit 10
#
# """
#
# #Do prawdzania czy są jakieś dziwne wartośći w kolumnach z danymi
# #query = """
# #    SELECT MIN(new_confirmed) AS min_confirmed, MAX(new_confirmed) AS max_confirmed
# #    FROM `bigquery-public-data.covid19_open_data.covid19_open_data`
# #    WHERE new_confirmed IS NOT NULL
# #"""
# #Dla new_confirmed: -5045418	5047094
#
# #query = """
# #    SELECT MIN(cumulative_confirmed) AS min_Cconfirmed, MAX(cumulative_confirmed) AS max_Cconfirmed
# #    FROM `bigquery-public-data.covid19_open_data.covid19_open_data`
# #    WHERE cumulative_confirmed IS NOT NULL
# #"""
# #Dla comulative_confirmed: 0	92440495
#
# #query = """
# #    SELECT MIN(new_deceased) AS min_deceased, MAX(new_deceased) AS max_deceased
# #    FROM `bigquery-public-data.covid19_open_data.covid19_open_data`
# #    WHERE new_deceased IS NOT NULL
# #"""
# #Dla new_deceased: -63811	63830
#
# #query = """
# #    SELECT MIN(cumulative_deceased) AS min_Cdeceased, MAX(cumulative_deceased) AS max_Cdeceased
# #    FROM `bigquery-public-data.covid19_open_data.covid19_open_data`
# #    WHERE cumulative_deceased IS NOT NULL
# #"""
# #DLa cumulative_deceased: 0	1005195
#
# #query = """
# #    SELECT MIN(cumulative_tested) AS min_Ctested, MAX(cumulative_tested) AS max_Ctested
# #    FROM `bigquery-public-data.covid19_open_data.covid19_open_data`
# #    WHERE cumulative_tested IS NOT NULL
# #"""
# #Dla cumulative_tested: 0	9214000000
#
# query_job = client.query(query)
# numeric_values_df = query_job.result().to_dataframe()
# numeric_values_df

In [41]:
# # 3.5. Sprawdź, jaki przedział czasowy jest uwzględniony w danych. Dodatkowo porównaj przedziały czasowe dla przypadków
# # nowych zachorowań, nowych śmierci oraz nowych zaszczepionych osób w danych.
#
# #Dla danych
# query = """
#     SELECT MIN(date) AS start_date, MAX(date) AS end_date
#     FROM `bigquery-public-data.covid19_open_data.covid19_open_data`
# """
# #Dało wynik 2020-01-01  2022-09-17
#
# #Dla nowych zachorowań
# query = """
#     SELECT MIN(date) AS start_date, MAX(date) AS end_date
#     FROM `bigquery-public-data.covid19_open_data.covid19_open_data`
#     WHERE new_confirmed IS NOT NULL AND new_confirmed != 0
# """
# #Dało wynik 2020-01-01  2022-09-15
#
# #Dla nowych śmierci
# query = """
#     SELECT MIN(date) AS start_date, MAX(date) AS end_date
#     FROM `bigquery-public-data.covid19_open_data.covid19_open_data`
#     WHERE new_deceased IS NOT NULL AND new_deceased != 0
# """
# #Dało wynik 2020-01-02  2022-09-15
#
# #Dla nowych zaszczepionych
# query = """
#     SELECT MIN(date) AS start_date, MAX(date) AS end_date
#     FROM `bigquery-public-data.covid19_open_data.covid19_open_data`
#     WHERE new_persons_vaccinated IS NOT NULL AND new_persons_vaccinated != 0
# """
# #Dało wynik 2020-12-07  2022-09-14
#
# query_job = client.query(query)
# time_range_df = query_job.result().to_dataframe()
# time_range_df

In [42]:
# # 3.6. Sprawdź więcej informacji (co najmniej 5 różnych) o danych dotyczących COVID-19. W tym celu nie wykonuj żadnych dodatkowych obliczeń.
# # Dodaliśmy limit 10, aby uruchomienie trwało szybciej
# #dane o hospitalizacji
# query = """
# select country_name, date, cumulative_hospitalized_patients, cumulative_intensive_care_patients, hospital_beds_per_1000
# from `bigquery-public-data.covid19_open_data.covid19_open_data`
# where cumulative_hospitalized_patients is not null
# limit 10
# """
# #informacje demograficzne o zakażeniach
# query = """
# select country_name, date, new_confirmed_male, new_confirmed_female
# from `bigquery-public-data.covid19_open_data.covid19_open_data`
# where population_male is not null and population_female is not null
# limit 10
# """
# #dane o testowaniu
# query = """
# select country_name, date, cumulative_tested, new_tested
# from `bigquery-public-data.covid19_open_data.covid19_open_data`
# where cumulative_tested is not null
# limit 10
# """
# #dane o szczepieniach
# query = """
# select country_name, date, cumulative_persons_fully_vaccinated, new_persons_fully_vaccinated
# from `bigquery-public-data.covid19_open_data.covid19_open_data`
# where cumulative_persons_fully_vaccinated is not null
# limit 10
# # """
# #zdrowie a zgony
# query = """
# select country_name, date, cumulative_deceased, health_expenditure_usd
# from `bigquery-public-data.covid19_open_data.covid19_open_data`
# where cumulative_deceased is not null and health_expenditure_usd is not null
# limit 10
# """
#
# query_job = client.query(query)
# data = query_job.result().to_dataframe()
# data


In [36]:
# 4.0
query = """
    select location_key, date, country_code, country_name,
    new_confirmed, new_deceased, cumulative_confirmed, cumulative_deceased, new_tested, cumulative_tested,
    new_persons_vaccinated, cumulative_persons_vaccinated, new_recovered,
    new_persons_fully_vaccinated, cumulative_persons_fully_vaccinated,
    population, population_male, population_female,
    population_density, human_development_index, gdp_usd,
    gdp_per_capita_usd, area_sq_km, vaccination_policy, stringency_index,
    life_expectancy, new_hospitalized_patients,
    population_age_00_09, population_age_10_19, population_age_20_29, population_age_30_39,
    population_density, smoking_prevalence, diabetes_prevalence, life_expectancy,
    cumulative_vaccine_doses_administered, new_vaccine_doses_administered
    from `bigquery-public-data.covid19_open_data.covid19_open_data` 
    where aggregation_level = 0
"""
#and (country_name = "Poland" or country_name = "Austria" or country_name = "Greece")

query_job = client.query(query)
df = query_job.result().to_dataframe()

df

location_key        date country_code country_name  new_confirmed  \
0              AT  2021-10-15           AT      Austria           2381   
1              AT  2022-04-02           AT      Austria          13858   
2              AT  2021-11-09           AT      Austria          11955   
3              AT  2022-01-16           AT      Austria          16095   
4              AT  2022-02-17           AT      Austria          30480   
5              AT  2020-03-16           AT      Austria            226   
6              AT  2022-06-25           AT      Austria           7001   
7              AT  2021-11-30           AT      Austria          10938   
8              AT  2021-07-16           AT      Austria            431   
9              AT  2021-03-01           AT      Austria           2169   
10             AT  2022-03-04           AT      Austria          31455   
11             AT  2022-02-24           AT      Austria          29741   
12             AT  2021-07-14           AT      Austria            302   
13             GR  2022-02-27           GR       Greece          16263   
14             GR  2020-02-06           GR       Greece              0   
15             GR  2020-09-08           GR       Greece            248   
16             GR  2021-01-22           GR       Greece            605   
17             GR  2022-07-05           GR       Greece          23364   
18             GR  2020-04-07           GR       Greece             52   
19             GR  2020-11-23           GR       Greece           2131   
20             GR  2020-07-22           GR       Greece             33   
21             GR  2021-06-14           GR       Greece            794   
22             GR  2021-08-12           GR       Greece           3493   
23             GR  2021-10-09           GR       Greece           1320   
24             GR  2022-01-25           GR       Greece          17960   
25             PL  2021-09-14           PL       Poland            767   
26             PL  2021-04-28           PL       Poland           8427   
27             PL  2021-03-15           PL       Poland          14396   
28             PL  2022-09-05           PL       Poland           4448   
29             PL  2022-08-25           PL       Poland           3928   
30             PL  2022-03-27           PL       Poland           6606   
31             PL  2020-09-07           PL       Poland            400   
32             PL  2020-03-20           PL       Poland            111   
33             PL  2022-07-27           PL       Poland           3391   
34             PL  2021-11-28           PL       Poland          13115   
35             PL  2021-11-17           PL       Poland          24882   
36             PL  2020-05-19           PL       Poland            471   
37             AT  2022-02-13           AT      Austria          23979   
38             AT  2021-08-06           AT      Austria            571   
39             AT  2022-06-03           AT      Austria           2691   
40             AT  2020-02-20           AT      Austria              0   
41             AT  2021-09-06           AT      Austria           1801   
42             AT  2020-07-10           AT      Austria            105   
43             AT  2021-08-18           AT      Austria           1293   
44             GR  2020-04-27           GR       Greece             32   
45             GR  2022-02-24           GR       Greece          15908   
46             GR  2022-09-15           GR       Greece           <NA>   
47             GR  2021-03-17           GR       Greece           3070   
48             GR  2022-04-17           GR       Greece           3953   
49             GR  2022-04-18           GR       Greece          10436   
50             GR  2021-06-05           GR       Greece            579   
51             GR  2022-06-09           GR       Greece           5052   
52             PL  2021-11-30           PL       Poland          29064   
53       

In [37]:
#4.01 czyszczenie danych
import numpy as np

# 1. Ogólne czyszczenie danych

# Konwersja kolumny date do formatu daty
df['date'] = pd.to_datetime(df['date'])

# Usunięcie duplikatów
df_clean = df.drop_duplicates()

# Usuwamy wiersze bez kluczowych informacji (np. brak kodu lub nazwy kraju)
df_clean = df_clean.dropna(subset=['country_code', 'country_name', 'new_confirmed', 'new_deceased', 'new_persons_vaccinated', 'population', 'gdp_usd', 'new_recovered',
                                   'new_persons_fully_vaccinated', 'new_hospitalized_patients', 'new_tested'])

# Ujednolicenie: ustawienie kodu kraju na wielkie litery
#df_clean['country_code'] = df_clean['country_code'].str.upper()

# Sprawdzamy dane liczbowe – ujemne wartości traktujemy jako błędne i ustawiamy jako NaN
num_cols = ['population', 'population_density', 'human_development_index', 
           'gdp_usd', 'gdp_per_capita_usd', 'area_sq_km', 'life_expectancy']
for col in num_cols:
    df_clean[col] = pd.to_numeric(df_clean[col], errors='coerce')
    df_clean.loc[df_clean[col] < 0, col] = np.nan

df_clean

Empty DataFrame
Columns: [location_key, date, country_code, country_name, new_confirmed, new_deceased, cumulative_confirmed, cumulative_deceased, new_tested, cumulative_tested, new_persons_vaccinated, cumulative_persons_vaccinated, new_recovered, new_persons_fully_vaccinated, cumulative_persons_fully_vaccinated, population, population_male, population_female, population_density, human_development_index, gdp_usd, gdp_per_capita_usd, area_sq_km, vaccination_policy, stringency_index, life_expectancy, new_hospitalized_patients, population_age_00_09, population_age_10_19, population_age_20_29, population_age_30_39, population_density_1, smoking_prevalence, diabetes_prevalence, life_expectancy_1, cumulative_vaccine_doses_administered, new_vaccine_doses_administered]
Index: []

In [28]:
#  4.1. Chcemy posiadać podstawowe dane o wszystkich krajach świata, które będą zrozumiałe dla człowieka oraz uniwersalne i 
#  potencjalnie przyszłościowe do dalszego przetwarzania.

countries_cols = [
    'country_code', 'country_name', 'population', 'population_male', 'population_female', 'population_density',
    'human_development_index', 'gdp_usd', 'gdp_per_capita_usd', 'area_sq_km', 'life_expectancy'
]
df_countries = df_clean[countries_cols].drop_duplicates()
# Opcjonalnie: usuwamy wiersze, gdzie brakuje kluczowych informacji o kraju
df_countries = df_countries.dropna(subset=['population', 'population_density', 'gdp_usd'])
# Propozycja naprawy błędnych danych: np. dla kolumn numerycznych warto sprawdzić, czy nie występują wartości ujemne
# i w razie ich wystąpienia zastąpić je np. zerem lub wartością mediany (tutaj tylko komentarz)

# Zapis do pliku CSV
df_countries.to_csv('4_1_countries_data.csv', index=False)

#df_countries

In [29]:
# 4.2. Chcemy wygenerować statystyki dotyczące zachorowań na COVID-19 na całym świecie.

cases_cols = [
    'location_key', 'date', 'country_code', 'country_name', 
    'new_confirmed', 'cumulative_confirmed', 'new_tested', 'cumulative_tested',
    'new_recovered', 'new_hospitalized_patients'
]
df_cases = df_clean[cases_cols].drop_duplicates()
df_cases = df_cases.dropna(subset=['date', 'new_confirmed', 'cumulative_confirmed']) # Usuwanie wierszy z brakującymi wartosciami
df_cases.to_csv('4_2_global_covid_cases.csv', index=False)

#df_cases

In [30]:
# 4.3. Chcemy poznać efekty COVID-19 poprzez uwypuklenie problemu śmiertelności ludzi spowodowanej wirusem.

mortality_cols = [
    'location_key', 'date', 'country_code', 'country_name', 
    'new_deceased', 'cumulative_deceased'
]
df_mortality = df_clean[mortality_cols].drop_duplicates()
df_mortality = df_mortality.dropna(subset=['date', 'new_deceased', 'cumulative_deceased'])
df_mortality.to_csv('4_3_covid_mortality.csv', index=False)

#df_mortality

In [32]:
# 4.4. Chcemy zaobserwować trendy i zależności dotyczące szczepień na COVID-19.

vaccination_cols = [
    'location_key', 'date', 'country_code', 'country_name', 
    'new_persons_vaccinated', 'cumulative_persons_vaccinated', 
    'new_persons_fully_vaccinated', 'cumulative_persons_fully_vaccinated',
    'population_age_00_09', 'population_age_10_19', 'population_age_20_29', 'population_age_30_39',
    'population_density', 'smoking_prevalence', 'diabetes_prevalence', 'life_expectancy',
    'cumulative_vaccine_doses_administered', 'new_vaccine_doses_administered'
]
df_vaccinations = df_clean[vaccination_cols].drop_duplicates()
df_vaccinations = df_vaccinations.dropna(subset=['date'])
df_vaccinations.to_csv('4_4_vaccination_trends.csv', index=False)

#df_vaccinations

In [33]:
# 4.5. Zdefiniuj własny dodatkowy przypadek.

# Przykładowo: Analiza związku między restrykcjami rządowymi (stringency_index) a liczbą nowych zachorowań
# Można wybrać coś ciekawszego tho
df_custom = df_clean[['date', 'country_name', 'stringency_index']].copy()
# Usuwamy rekordy, w których brakuje krytycznych informacji
df_custom = df_custom.drop_duplicates().dropna(subset=['date', 'stringency_index'])
df_custom.to_csv('4_5_custom_case.csv', index=False)

#df_custom

In [34]:
#5.0
# Dataframey powstałe w części 4
# df_countries         - dane statyczne o krajach (4.1)
# df_cases             - dane dotyczące zachorowań (4.2)
# df_mortality         - dane dotyczące śmiertelności (4.3)
# df_vaccinations      - dane dotyczące szczepień (4.4)
# df_custom           - dane customowe(4.5)

# 1. Łączenie danych czasowych
# Klucz łączący to: "location_key", "date", "country_code", "country_name"

# Łączymy dane dotyczące zachorowań i śmiertelności
df_time_series = pd.merge(
    df_cases, df_mortality,
    on=["location_key", "date", "country_code", "country_name"],
    how="outer"
)

# Dołączamy dane dotyczące szczepień
df_time_series = pd.merge(
    df_time_series, df_vaccinations,
    on=["location_key", "date", "country_code", "country_name"],
    how="outer"
)

# Upewnij się, że kolumna 'date' w obu DataFrame’ach jest w formacie datetime64[ns]
df_time_series['date'] = pd.to_datetime(df_time_series['date'])
df_custom['date'] = pd.to_datetime(df_custom['date'])

# Dołączamy dane dotyczące testów
df_time_series = pd.merge(
    df_time_series, df_custom,
    on=["date", "country_name"],
    how="outer"
)

# df_countries nie zawiera kolumny 'date', dlatego łączymy je na podstawie wspólnych kluczy: "country_code" i "country_name"
df_final = pd.merge(
    df_time_series, df_countries,
    on=["country_code", "country_name"],
    how="left"
)

# Usuwamy ewentualne duplikaty
df_final = df_final.drop_duplicates()

# Sortujemy dane – najczęściej po kodzie kraju i dacie, by mieć ujednoliconą strukturę
df_final = df_final.sort_values(by=["country_code", "date"])

# Zapisujemy wynik do pliku CSV
df_final.to_csv("5.0_combined_covid_data.csv", index=False)

#df_final

In [35]:
#6.0
# 1. Wczytanie danych z części 5
df_covid = pd.read_csv("5.0_combined_covid_data.csv", parse_dates=["date"])

# 2. Wczytanie danych z world_countries.csv
df_world = pd.read_csv("world_countries.csv")
# Zmieniamy nazwę kolumny "Country/Territories" na "country_name" dla ułatwienia łączenia
df_world.rename(columns={"Country/Territory": "country_name"}, inplace=True)

# 3. Wczytanie danych z GDP.csv
df_gdp = pd.read_csv("GDP.csv")
# Zmieniamy nazwę kolumny "Country Name" na "country_name"
df_gdp.rename(columns={"Country Name": "country_name"}, inplace=True)

# 4. Normalizacja kluczy łączenia (pełne nazwy krajów) we wszystkich DataFrame'ach
df_covid["country_name"] = df_covid["country_name"].str.strip().str.lower()
df_world["country_name"] = df_world["country_name"].str.strip().str.lower()
df_gdp["country_name"] = df_gdp["country_name"].str.strip().str.lower()

# 5. Dla danych covidowych wyodrębniamy rok z kolumny "date", by móc łączyć z danymi PKB
df_covid["year"] = df_covid["date"].dt.year

# 6. Łączenie danych
# 6.1. Łączymy dane covidowe z danymi krajowymi (world_countries.csv) – łączymy po "country_name"
df_merged = pd.merge(df_covid, df_world, on="country_name", how="left")

# 6.2. Łączymy wynik z danymi PKB. W df_gdp kolumna z rokiem to zazwyczaj "Year", więc łączymy:
df_merged = pd.merge(df_merged, df_gdp, left_on=["country_name", "year"], 
                     right_on=["country_name", "Year"], how="left")
# Połączone dane mają już dwie kolumny określające rok, więc możemy usunąć zbędną kolumnę "Year":
df_merged.drop(columns=["Year"], inplace=True)

# 7. Usunięcie zbędnych kolumn: 'area_sq_km', 'Country Code', 'Value'
df_merged = df_merged.drop(columns=['area_sq_km', 'Country Code', 'Value'], errors='ignore')

# 8. Finalne czyszczenie danych – usunięcie duplikatów itp.
df_merged.drop_duplicates(inplace=True)

# df_pivoted = df_merged.pivot(['country_code', 'country_name'],)
# 9. Zapisanie wyniku do pliku CSV
df_merged.to_csv("6.0_combined_covid_world_gdp_data.csv", index=False)

#Dane z części 5 oraz pliki world_countries.csv i GDP.csv zostały połączone i zapisane do pliku combined_covid_world_gdp_data.csv."
